In [1]:
import os
import gc
import random
from pathlib import Path

import datasets
import nltk
import numpy as np
import pandas as pd
import torch
import transformers

from datasets import Dataset, concatenate_datasets
from evaluate import combine, load
from functional import seq
from huggingface_hub import notebook_login
from IPython.display import HTML, display
from transformers import (AutoModelForSeq2SeqLM, AutoTokenizer,
                          DataCollatorForSeq2Seq, GenerationConfig,
                          Seq2SeqTrainer, Seq2SeqTrainingArguments)

from funcutils import get

os.environ["TOKENIZERS_PARALLELISM"] = "true"
# os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "max_split_size_mb:512"
assert torch.cuda.is_available()

NUM_TRAIN_EPOCHS = 5
TASK = 'mt' # 'd2s' or 's2d' or 'mt' pull from argv
MODEL_CKPNT = "t5-small" # t5-small or t5-base
NATURAL_LANGUAGE = "nl"
STRUCTURED_DATA = "sd"
LR = 2.0e-4
TRAIN_CHKPNT_NAME = f"models/{MODEL_CKPNT}-finetuned-webnlg-{TASK}-{LR:.1e}"

TARGET = NATURAL_LANGUAGE if TASK == 'd2s' else STRUCTURED_DATA 
INPUT = STRUCTURED_DATA if TASK == 'd2s' else NATURAL_LANGUAGE 

In [2]:
assert TARGET != INPUT
del NATURAL_LANGUAGE
del STRUCTURED_DATA

In [3]:
tokenizer = AutoTokenizer.from_pretrained(MODEL_CKPNT)

In [4]:
max_input_length = 256
max_target_length = 256
tokenize = lambda x: tokenizer(x, max_length = max_input_length, truncation=True, padding=True)
tokenize

<function __main__.<lambda>(x)>

In [5]:
device = "cuda:0" if torch.cuda.is_available() else "cpu"
model = AutoModelForSeq2SeqLM.from_pretrained(MODEL_CKPNT)
model = model.to(device)
model

T5ForConditionalGeneration(
  (shared): Embedding(32128, 512)
  (encoder): T5Stack(
    (embed_tokens): Embedding(32128, 512)
    (block): ModuleList(
      (0): T5Block(
        (layer): ModuleList(
          (0): T5LayerSelfAttention(
            (SelfAttention): T5Attention(
              (q): Linear(in_features=512, out_features=512, bias=False)
              (k): Linear(in_features=512, out_features=512, bias=False)
              (v): Linear(in_features=512, out_features=512, bias=False)
              (o): Linear(in_features=512, out_features=512, bias=False)
              (relative_attention_bias): Embedding(32, 8)
            )
            (layer_norm): T5LayerNorm()
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (1): T5LayerFF(
            (DenseReluDense): T5DenseActDense(
              (wi): Linear(in_features=512, out_features=2048, bias=False)
              (wo): Linear(in_features=2048, out_features=512, bias=False)
              (dropout): Drop

In [6]:
generation_config = GenerationConfig.from_pretrained(MODEL_CKPNT)
generation_config.min_length = 5
generation_config.num_beams = 4
generation_config.max_length = 2048
generation_config.early_stopping = True
generation_config.no_repeat_ngram_size = 2
generation_config.temperature = .9

In [7]:
batch_size = 64 if MODEL_CKPNT == "t5-small" else 16
# START: ADAPTED FROM https://huggingface.co/docs/transformers/tasks/summarization
args = Seq2SeqTrainingArguments(
    TRAIN_CHKPNT_NAME,
    eval_steps=1500,
    evaluation_strategy = "steps",
    learning_rate=LR,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size//2,
    gradient_accumulation_steps=2 if MODEL_CKPNT != 't5-small' else 1, # so we have an effective batch size of 32
    weight_decay=0.01,
    save_total_limit=5,
    num_train_epochs=NUM_TRAIN_EPOCHS,
    predict_with_generate=True,
    fp16=True,
    push_to_hub=False,
    save_steps=600,
    generation_config=generation_config,
    generation_max_length=200,
)
# END: ADAPTED FROM https://huggingface.co/docs/transformers/tasks/summarization

In [8]:
data_collator = DataCollatorForSeq2Seq(tokenizer, model=model)
metric = combine([
    load("rouge"),
])
metric

In [9]:
# START: COPIED FROM https://huggingface.co/docs/transformers/tasks/summarization
def compute_metrics(eval_pred):
    # monitor memory and force gc. probably slows us down, probably 
    torchmem = torch.cuda.memory_allocated()
    torchcap = torch.cuda.get_device_properties(0).total_memory

    print(f"torch has allocated {torchmem} of {torchcap}")

    predictions, labels = eval_pred
    predictions = np.where(predictions != -100, predictions, tokenizer.pad_token_id)
    decoded_preds = tokenizer.batch_decode(predictions, skip_special_tokens=True)

    labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)

    # Rouge expects a newline after each sentence
    decoded_preds = ["\n".join(nltk.sent_tokenize(pred.strip())) for pred in decoded_preds]
    decoded_labels = ["\n".join(nltk.sent_tokenize(label.strip())) for label in decoded_labels]

    result = metric.compute(predictions=decoded_preds, references=decoded_labels)

    # Add mean generated length
    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in predictions]
    result["gen_len"] = np.mean(prediction_lens)
    return result
# END: COPIED FROM https://huggingface.co/docs/transformers/tasks/summarization

In [10]:
df = pd.read_pickle("~/repos/nlgs-research/pipeline/normalized_data/webnlg_clean.pkl")
df

subset    category  index  \
0        dev     Airport      0   
1        dev     Airport      1   
2        dev     Airport      2   
3        dev     Airport      3   
4        dev     Airport      4   
...      ...         ...    ...   
16090   test  University   1595   
16091   test  University   1596   
16092   test  University   1597   
16093   test  University   1598   
16094   test  University   1599   

                                                      sd  \
0                    Aarhus|leader name|Jacob Bundsgaard   
1                    Aarhus Airport|runway length|2702.0   
2      Adirondack Regional Airport|elevation above th...   
3      Adirondack Regional Airport|location|Harrietst...   
4      Adolfo Suarez Madrid-Barajas Airport|location|...   
...                                                  ...   
16090  Acharya Institute of Technology|was given the ...   
16091  Romania|ethnic group|Germans of Romania; Roman...   
16092  School of Business and Social Sciences at the ...   
16093  School of Business and Social Sciences at the ...   
16094  School of Business and Social Sciences at the ...   

                                                      nl  
0            [The leader of Aarhus is Jacob Bundsgaard.]  
1      [Aarhus Airport's runway length is 2702.0., Th...  
2      [Adirondack Regional Airport is 507 metres abo...  
3      [Adirondack Regional airport is located at Har...  
4      [Adolfo Suarez Madrid-Barajas Airport is found...  
...                                                  ...  
16090  [The Acharya Institute of Technology in Karnat...  
16091  [The Germans of Romania are one of the ethnic ...  
16092  [The School of Business and Social Sciences at...  
16093  [Denmark is led by the Monarchy of Demark and ...  
16094  [The School of Business and Social Sciences at...  

[16095 rows x 5 columns]

 we must invent `seed_number` since d2s can output multiple sentences for the
 same data input. So the seed will be a generation parameter, in the case that
 we are working in a deterministic environment, so generation can vary as
 desired. This computes a cartesian product.

In [11]:
cartesian_sd_nl = []
for (i, subset, cat, indx, sd, nl) in df.itertuples():
    for j, nl_option in enumerate(nl):
        pairing = dict(
            record_idx=i,
            seed_number=j,
            subset=subset,
            category=cat,
            split_index=indx,
            sd=sd,
            nl=nl_option,
            task=TASK if TASK != 'mt' else 's2d' 
        )
        cartesian_sd_nl.append(pairing)
        if TASK == "mt":
            reverse_pair = pairing.copy()
            reverse_pair['sd'] = nl_option
            reverse_pair['nl'] = sd
            reverse_pair['task'] = 'd2s'
            cartesian_sd_nl.append(reverse_pair)

# calling this "flattened" because it no longer has nested records
has_not_run = True
flt = pd.DataFrame(cartesian_sd_nl)
flt

record_idx  seed_number subset    category  split_index  \
0               0            0    dev     Airport            0   
1               0            0    dev     Airport            0   
2               1            0    dev     Airport            1   
3               1            0    dev     Airport            1   
4               1            1    dev     Airport            1   
...           ...          ...    ...         ...          ...   
85779       16093            1   test  University         1598   
85780       16093            2   test  University         1598   
85781       16093            2   test  University         1598   
85782       16094            0   test  University         1599   
85783       16094            0   test  University         1599   

                                                      sd  \
0                    Aarhus|leader name|Jacob Bundsgaard   
1              The leader of Aarhus is Jacob Bundsgaard.   
2                    Aarhus Airport|runway length|2702.0   
3              Aarhus Airport's runway length is 2702.0.   
4                    Aarhus Airport|runway length|2702.0   
...                                                  ...   
85779  The School of Business and Social Sciences at ...   
85780  School of Business and Social Sciences at the ...   
85781  The School of Business and Social Sciences at ...   
85782  School of Business and Social Sciences at the ...   
85783  The School of Business and Social Sciences at ...   

                                                      nl task  
0              The leader of Aarhus is Jacob Bundsgaard.  s2d  
1                    Aarhus|leader name|Jacob Bundsgaard  d2s  
2              Aarhus Airport's runway length is 2702.0.  s2d  
3                    Aarhus Airport|runway length|2702.0  d2s  
4      The Aarhus Airport has a runway length of 2702.0.  s2d  
...                                                  ...  ...  
85779  School of Business and Social Sciences at the ...  d2s  
85780  The School of Business and Social Sciences at ...  s2d  
85781  School of Business and Social Sciences at the ...  d2s  
85782  The School of Business and Social Sciences at ...  s2d  
85783  School of Business and Social Sciences at the ...  d2s  

[85784 rows x 8 columns]

In [12]:
# prepend the seed number. This should be rt of the prompt hereafter for `d2s`
# tasks. So, prompting with two different numbers should never generate the same
# output.

if (TASK == "mt") and has_not_run:
    has_not_run = False
    flt['sd'] = flt.task + flt.seed_number.map(lambda x: " " + str(x) + ": ") + flt.sd
flt

record_idx  seed_number subset    category  split_index  \
0               0            0    dev     Airport            0   
1               0            0    dev     Airport            0   
2               1            0    dev     Airport            1   
3               1            0    dev     Airport            1   
4               1            1    dev     Airport            1   
...           ...          ...    ...         ...          ...   
85779       16093            1   test  University         1598   
85780       16093            2   test  University         1598   
85781       16093            2   test  University         1598   
85782       16094            0   test  University         1599   
85783       16094            0   test  University         1599   

                                                      sd  \
0             s2d 0: Aarhus|leader name|Jacob Bundsgaard   
1       d2s 0: The leader of Aarhus is Jacob Bundsgaard.   
2             s2d 0: Aarhus Airport|runway length|2702.0   
3       d2s 0: Aarhus Airport's runway length is 2702.0.   
4             s2d 1: Aarhus Airport|runway length|2702.0   
...                                                  ...   
85779  d2s 1: The School of Business and Social Scien...   
85780  s2d 2: School of Business and Social Sciences ...   
85781  d2s 2: The School of Business and Social Scien...   
85782  s2d 0: School of Business and Social Sciences ...   
85783  d2s 0: The School of Business and Social Scien...   

                                                      nl task  
0              The leader of Aarhus is Jacob Bundsgaard.  s2d  
1                    Aarhus|leader name|Jacob Bundsgaard  d2s  
2              Aarhus Airport's runway length is 2702.0.  s2d  
3                    Aarhus Airport|runway length|2702.0  d2s  
4      The Aarhus Airport has a runway length of 2702.0.  s2d  
...                                                  ...  ...  
85779  School of Business and Social Sciences at the ...  d2s  
85780  The School of Business and Social Sciences at ...  s2d  
85781  School of Business and Social Sciences at the ...  d2s  
85782  The School of Business and Social Sciences at ...  s2d  
85783  School of Business and Social Sciences at the ...  d2s  

[85784 rows x 8 columns]

In [13]:
tokenized = tokenize(list(flt[INPUT].values))

 !!Heads-up!! The following fields comprise the "interface" of the model,
 despite the fact the documentation doesn't make this obvious. Without these
 particular names, ['input_ids', 'attention_mask', 'labels'],
 the model will not train and provide cryptic error messges.

In [14]:
flt['input_ids'] = tokenized['input_ids']
flt['attention_mask'] = tokenized['attention_mask']
flt['labels'] = flt[TARGET].map(lambda x: tokenize(x)['input_ids'])
flt['input_ids'].map(len)

0        184
1        184
2        184
3        184
4        184
        ... 
85779    184
85780    184
85781    184
85782    184
85783    184
Name: input_ids, Length: 85784, dtype: int64

In [15]:
# this will keep only the needed fields in memory on the GPU
def pd_to_dataset(df: pd.DataFrame, split='train') -> Dataset:
    d = df[df.subset== split ][['input_ids','attention_mask','labels']]
    return Dataset.from_pandas(d)
        
# get_ds alias should bake in the desired argument. Makes you wish python
# supported currying
get_ds = lambda x: pd_to_dataset(flt, x)
tds = get_ds('train')
eds = get_ds('dev')

In [16]:
trainer = Seq2SeqTrainer(
    model,
    args,
    train_dataset=tds,
    eval_dataset=eds,
    data_collator=data_collator,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics,
)

In [17]:
# we must try-catch because resume_from_checkpoint throws a value error (for
# some reason instead of raising a warning) if training did not begin first.
try:
    trainer.train(resume_from_checkpoint=True)
except ValueError as e:
    print(e)
    trainer.train()

/home/vente/.conda/envs/nlgs/lib/python3.9/site-packages/transformers/optimization.py:407: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
You're using a T5TokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


No valid checkpoint found in output directory (models/t5-small-finetuned-webnlg-mt-2.0e-04)


/home/vente/.conda/envs/nlgs/lib/python3.9/site-packages/transformers/generation/utils.py:1255: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use a generation configuration file (see https://huggingface.co/docs/transformers/main_classes/text_generation)
  warnings.warn(


torch has allocated 768734208 of 25447170048
torch has allocated 768734208 of 25447170048
torch has allocated 768458240 of 25447170048


In [18]:
try:
    del tds
    del eds
    del tds
except Exception as e:
    print(e)

name 'tds' is not defined


In [19]:
tds = get_ds('test')
# debug = Dataset.from_dict(tds[0:2])
predictions = trainer.predict(tds)
predictions

torch has allocated 770040320 of 25447170048


PredictionOutput(predictions=array([[   0,    3,    7, ..., -100, -100, -100],
       [   0,    3,   26, ..., -100, -100, -100],
       [   0,    3,    7, ..., -100, -100, -100],
       ...,
       [   0,    3,   26, ...,    0,    0,    0],
       [   0,    3,    7, ...,    0,    0,    0],
       [   0,    3,   26, ...,    0,    0,    0]]), label_ids=array([[   3,    7,  357, ..., -100, -100, -100],
       [   3,   26,  357, ..., -100, -100, -100],
       [   3,    7,  357, ..., -100, -100, -100],
       ...,
       [   3,   26,  357, ..., -100, -100, -100],
       [   3,    7,  357, ..., -100, -100, -100],
       [   3,   26,  357, ..., -100, -100, -100]]), metrics={'test_loss': 0.3367599844932556, 'test_rouge1': 0.8259028497286737, 'test_rouge2': 0.6516027777926748, 'test_rougeL': 0.7051514372474443, 'test_rougeLsum': 0.729753988119749, 'test_gen_len': 43.19898200757576, 'test_runtime': 118.913, 'test_samples_per_second': 71.044, 'test_steps_per_second': 2.22})

In [20]:
flat_keep_positive = lambda x: [e for e in x if e > 1]
pred_df = pd.DataFrame(columns=['pred_ids'], data=pd.Series(list(predictions.predictions)))
decoded = pred_df.pred_ids.map(flat_keep_positive).map(tokenizer.decode)
pred_df['decoded'] = decoded
pred_df['subset'] = 'test'
pred_df

pred_ids  \
0     [0, 3, 7, 357, 26, 209, 10, 891, 23, 14205, 76...   
1     [0, 3, 26, 357, 7, 3, 632, 10, 891, 23, 14205,...   
2     [0, 3, 7, 357, 26, 209, 10, 891, 23, 14205, 76...   
3     [0, 3, 26, 357, 7, 3, 632, 10, 891, 23, 14205,...   
4     [0, 3, 7, 357, 26, 209, 10, 1980, 32, 40, 89, ...   
...                                                 ...   
8443  [0, 3, 26, 357, 7, 3, 632, 10, 37, 1121, 13, 1...   
8444  [0, 3, 7, 357, 26, 209, 10, 1121, 13, 1769, 11...   
8445  [0, 3, 26, 357, 7, 3, 632, 10, 37, 1121, 13, 1...   
8446  [0, 3, 7, 357, 26, 209, 10, 1121, 13, 1769, 11...   
8447  [0, 3, 26, 357, 7, 209, 10, 37, 1121, 13, 1769...   

                                                decoded subset  
0     s2d 1: Abilene Regional Airport|city served|Ab...   test  
1     d2s 0: Abilene Regional Airport serves the cit...   test  
2     s2d 1: Abilene Regional Airport|city served|Ab...   test  
3     d2s 0: Abilene Regional Airport serves the cit...   test  
4     s2d 1: Adolfo Suarez Madrid-Barajas Airport|lo...   test  
...                                                 ...    ...  
8443  d2s 0: The School of Business and Social Scien...   test  
8444  s2d 1: School of Business and Social Sciences ...   test  
8445  d2s 0: The School of Business and Social Scien...   test  
8446  s2d 1: School of Business and Social Sciences ...   test  
8447  d2s 1: The School of Business and Social Scien...   test  

[8448 rows x 3 columns]

In [21]:
test_set = flt[flt.subset == 'test'].copy()
test_set['pred_ids'] = list(pred_df['pred_ids'].values)
test_set['decoded'] = list(pred_df['decoded'].values)
test_set

record_idx  seed_number subset    category  split_index  \
77336       14495            0   test     Airport            0   
77337       14495            0   test     Airport            0   
77338       14495            1   test     Airport            0   
77339       14495            1   test     Airport            0   
77340       14496            0   test     Airport            1   
...           ...          ...    ...         ...          ...   
85779       16093            1   test  University         1598   
85780       16093            2   test  University         1598   
85781       16093            2   test  University         1598   
85782       16094            0   test  University         1599   
85783       16094            0   test  University         1599   

                                                      sd  \
77336  s2d 0: Abilene Regional Airport|city served|Ab...   
77337  d2s 0: Abilene, Texas is served by the Abilene...   
77338  s2d 1: Abilene Regional Airport|city served|Ab...   
77339  d2s 1: Abilene Regional Airport serves the cit...   
77340  s2d 0: Adolfo Suarez Madrid-Barajas Airport|lo...   
...                                                  ...   
85779  d2s 1: The School of Business and Social Scien...   
85780  s2d 2: School of Business and Social Sciences ...   
85781  d2s 2: The School of Business and Social Scien...   
85782  s2d 0: School of Business and Social Sciences ...   
85783  d2s 0: The School of Business and Social Scien...   

                                                      nl task  \
77336  Abilene, Texas is served by the Abilene region...  s2d   
77337  Abilene Regional Airport|city served|Abilene, ...  d2s   
77338  Abilene Regional Airport serves the city of Ab...  s2d   
77339  Abilene Regional Airport|city served|Abilene, ...  d2s   
77340  Adolfo Suarez Madrid-Barajas Airport can be fo...  s2d   
...                                                  ...  ...   
85779  School of Business and Social Sciences at the ...  d2s   
85780  The School of Business and Social Sciences at ...  s2d   
85781  School of Business and Social Sciences at the ...  d2s   
85782  The School of Business and Social Sciences at ...  s2d   
85783  School of Business and Social Sciences at the ...  d2s   

                                               input_ids  \
77336  [891, 23, 14205, 6, 2514, 19, 2098, 57, 8, 891...   
77337  [891, 23, 14205, 7676, 5735, 9175, 6726, 2098,...   
77338  [891, 23, 14205, 7676, 5735, 4657, 8, 690, 13,...   
77339  [891, 23, 14205, 7676, 5735, 9175, 6726, 2098,...   
77340  [1980, 32, 40, 89, 32, 1923, 9, 2638, 12033, 1...   
...                                                  ...   
85779  [1121, 13, 1769, 11, 2730, 9226, 44, 8, 71, 29...   
85780  [37, 1121, 13, 1769, 11, 2730, 9226, 44, 8, 71...   
85781  [1121, 13, 1769, 11, 2730, 9226, 44, 8, 71, 29...   
85782  [37, 1121, 13, 1769, 11, 2730, 9226, 44, 8, 71...   
85783  [1121, 13, 1769, 11, 2730, 9226, 44, 8, 71, 29...   

                                          attention_mask  \
77336  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
77337  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
77338  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
77339  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
77340  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
...                                                  ...   
85779  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
85780  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
85781  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
85782  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
85783  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   

                                                  labels  \
77336  [3, 7, 357, 26, 3, 632, 10, 891, 23, 14205, 76...   
77337  [3, 26, 357, 7, 3, 632, 10, 891, 23, 14205, 6,...   
77338  [3, 7, 357, 26, 209, 10, 891, 23, 14205, 7676,...   
77339  [3, 26, 357, 7, 209, 10

In [22]:
save_fname = f"~/repos/nlgs-research/pipeline/predictions/{TASK}-{MODEL_CKPNT}-{NUM_TRAIN_EPOCHS}.pkl"
test_set.to_pickle(save_fname)
save_fname

'~/repos/nlgs-research/pipeline/predictions/mt-t5-small-5.pkl'

 ## Sanity Checks

In [23]:
def text_to_prediction_single(text):
    tensors = tokenizer("<pad>" + text + "</s>", return_tensors='pt').to(device)['input_ids']
    generation = trainer.model.generate(tensors,
        early_stopping=True,
        num_beams=5,
        max_new_tokens=1024,
        temperature=.9,
    ) 
    return tokenizer.decode(generation[0], skip_special_tokens=True)

t = "The leader of Aarhus is Jacob Bundsgaard."
text_to_prediction_single(t)

's2d 1: Aarhus|leader name|Jacob Bundsgaard'

In [24]:
print("\n".join(map(tokenizer.decode,
                np.where(predictions.predictions != -100, predictions.predictions, tokenizer.pad_token_id)
                )))

<pad> s2d 1: Abilene Regional Airport|city served|Abilene, Texas</s><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad>
<pad> d2s 0: Abilene Regional Airport ser

In [25]:
if TASK == "mt":
    print("\n".join(map(text_to_prediction_single, [
        'd2s 0: Aarhus|leader name|Jacob Bundsgaard',
        'd2s 1: Aarhus|leader name|Jacob Bundsgaard',
        "d2s 0: United States|leader name|Barack Obama ",
        's2d 0: The leader of Aarhus is Jacob Bundsgaard.',
        "s2d 0: Linus Torvalds was born in Helsinki, Finland. He is the son of journalists Anna and Nils Torvalds",
        "s2d 1: Linus Torvalds was born in Helsinki, Finland. He is the son of journalists Anna and Nils Torvalds",
    ])))
else:
    print("\n".join(map(text_to_prediction_single, [
        'Aarhus|leader name|Jacob Bundsgaard',
        'Aarhus|leader name|Jacob Bundsgaard',
        "United States|leader name|Barack Obama ",
        'The leader of Aarhus is Jacob Bundsgaard.',
        "Linus Torvalds was born in Helsinki, Finland. He is the son of journalists Anna and Nils Torvalds",
        "Linus Torvalds was born in Helsinki, Finland. He is the son of journalists Anna and Nils Torvalds",
    ])))

d2s 0: The leader of Aarhus is Jacob Bundsgaard.
d2s 1: The leader of Aarhus is Jacob Bundsgaard.
d2s 0: Barack Obama is the leader of the United States.
s2d 1: Aarhus|leader name|Jacob Bundsgaard
s2d 0: Linus Torvalds|birth place|Finland; Linus Torvalds|successor|Anna and Nils Torvalds
s2d 1: Linus Torvalds|birth place|Finland; Linus Torvalds|successor|Anna and Nils Torvalds
